In [1]:
import os
import argparse
import numpy as np
import pandas as pd

from sklearn import preprocessing
from sklearn.metrics import log_loss
from sklearn.preprocessing import StandardScaler, QuantileTransformer
from sklearn.decomposition import PCA

import torch
import torch.nn as nn
import torch.nn.functional as F

import pytorch_lightning as pl

!pip install ../input/iterativestratification/
from iterstrat.ml_stratifiers import MultilabelStratifiedKFold

from datetime import datetime
kernel_start = datetime.now()

Processing d:\github\kaggle-lish-moa\input\iterativestratification
  Created wheel for iterative-stratification: filename=iterative_stratification-0.1.6-py3-none-any.whl size=8406 sha256=7fe433a39360f08458965593e194a66099dddfef51c707e6aa0b1e5662242529
  Stored in directory: C:\Users\mkwasnia\AppData\Local\Temp\pip-ephem-wheel-cache-l5g5_9m6\wheels\6b\3c\16\652e67f5a1dbee68df84bc17ddca565340c7a48f0a9d5ba43c
Successfully built iterative-stratification
  Attempting uninstall: iterative-stratification
    Found existing installation: iterative-stratification 0.1.6
    Uninstalling iterative-stratification-0.1.6:
      Successfully uninstalled iterative-stratification-0.1.6


In [2]:
cfg = argparse.Namespace()
cfg.n_seeds = 5
cfg.n_splits = 5
cfg.n_units = 512
cfg.lr_sched_factor = 0.4
cfg.batch_size_exp = 7
# cfg.lr = 1e-3
# cfg.dropout_1 = 0.4785613243415906
# cfg.dropout_2 = 0.2867998721177728
# cfg.w_decay = 4.485092595065505e-06

In [4]:
from model import MoANeuralNetwork

In [5]:
input_dir = '../input/lish-moa'

# Read
train_features = pd.read_csv(os.path.join(input_dir, 'train_features.csv'))
train_targets_scored = pd.read_csv(os.path.join(input_dir, 'train_targets_scored.csv'))
test_features = pd.read_csv(os.path.join(input_dir, 'test_features.csv'))

# Feature cols (genes and cells)
GENES = [col for col in train_features.columns if col.startswith('g-')]
CELLS = [col for col in train_features.columns if col.startswith('c-')]

# Quantile transformation
for col in (GENES + CELLS):
    transformer = QuantileTransformer(n_quantiles=100,random_state=0, output_distribution="normal")
    train_len = len(train_features[col].values)
    test_len  = len(test_features[col].values)
    raw_vec = train_features[col].values.reshape(train_len, 1)
    transformer.fit(raw_vec)

    train_features[col] = transformer.transform(raw_vec).reshape(1, train_len)[0]
    test_features[col] = transformer.transform(test_features[col].values.reshape(test_len, 1)).reshape(1, test_len)[0]
    
print(f'Train {train_features.shape} test {test_features.shape}')

Train (23814, 876) test (3982, 876)


In [6]:
n_comp = 500

comb_features = pd.concat([pd.DataFrame(train_features[GENES]), pd.DataFrame(test_features[GENES])])
comb_features_pca = PCA(n_components=n_comp, random_state=42).fit_transform(comb_features[GENES])

train2 = comb_features_pca[:train_features.shape[0]]
test2  = comb_features_pca[-test_features.shape[0]:]
train2 = pd.DataFrame(train2, columns=[f'pca_G-{i}' for i in range(n_comp)])
test2  = pd.DataFrame(test2, columns=[f'pca_G-{i}' for i in range(n_comp)])

train_features = pd.concat((train_features, train2), axis=1)
test_features  = pd.concat((test_features, test2), axis=1)

n_comp = 50

comb_features = pd.concat([pd.DataFrame(train_features[CELLS]), pd.DataFrame(test_features[CELLS])])
comb_features_pca = PCA(n_components=n_comp, random_state=42).fit_transform(comb_features[CELLS])

train2 = comb_features_pca[:train_features.shape[0]]
test2  = comb_features_pca[-test_features.shape[0]:]
train2 = pd.DataFrame(train2, columns=[f'pca_C-{i}' for i in range(n_comp)])
test2  = pd.DataFrame(test2, columns=[f'pca_C-{i}' for i in range(n_comp)])

train_features = pd.concat((train_features, train2), axis=1)
test_features  = pd.concat((test_features, test2), axis=1)

print(f'Train {train_features.shape} test {test_features.shape}')

Train (23814, 1526) test (3982, 1526)


In [7]:
var_thresh = VarianceThreshold(0.8)
data = train_features.append(test_features)
data_transformed = var_thresh.fit_transform(data.iloc[:, 4:])

train_features_transformed = data_transformed[ : train_features.shape[0]]
test_features_transformed  = data_transformed[-test_features.shape[0] : ]

train_features = pd.DataFrame(
    train_features[['sig_id','cp_type','cp_time','cp_dose']].values.reshape(-1, 4),
    columns=['sig_id','cp_type','cp_time','cp_dose'])

train_features = pd.concat([train_features, pd.DataFrame(train_features_transformed)], axis=1)

test_features = pd.DataFrame(
    test_features[['sig_id','cp_type','cp_time','cp_dose']].values.reshape(-1, 4),
    columns=['sig_id','cp_type','cp_time','cp_dose'])

test_features = pd.concat([test_features, pd.DataFrame(test_features_transformed)], axis=1)

print(f'Train {train_features.shape} test {test_features.shape}')

Train (23814, 1040) test (3982, 1040)


In [10]:
def fe_stats(train, test):
    
    features_g = list(train.columns[4:776])
    features_c = list(train.columns[776:876])
    
    for df in train, test:
        df['g_sum'] = df[features_g].sum(axis = 1)
        df['g_mean'] = df[features_g].mean(axis = 1)
        df['g_std'] = df[features_g].std(axis = 1)
        df['g_kurt'] = df[features_g].kurtosis(axis = 1)
        df['g_skew'] = df[features_g].skew(axis = 1)
        df['c_sum'] = df[features_c].sum(axis = 1)
        df['c_mean'] = df[features_c].mean(axis = 1)
        df['c_std'] = df[features_c].std(axis = 1)
        df['c_kurt'] = df[features_c].kurtosis(axis = 1)
        df['c_skew'] = df[features_c].skew(axis = 1)
        df['gc_sum'] = df[features_g + features_c].sum(axis = 1)
        df['gc_mean'] = df[features_g + features_c].mean(axis = 1)
        df['gc_std'] = df[features_g + features_c].std(axis = 1)
        df['gc_kurt'] = df[features_g + features_c].kurtosis(axis = 1)
        df['gc_skew'] = df[features_g + features_c].skew(axis = 1)
        
    return train, test

train_features, test_features = fe_stats(train_features, test_features)

In [11]:
train_data = train_features.merge(train_targets_scored, on='sig_id')
train_data = train_data[train_data['cp_type']!='ctl_vehicle'].reset_index(drop=True)

test_data  = test_features

print(f'Train {train_data.shape} test {test_data.shape}')

Train (21948, 1261) test (3982, 1055)


In [13]:
target_cols = train_data[train_targets_scored.columns]
target_cols = target_cols.drop('sig_id', axis=1).columns.values.tolist()

#target_cols

['5-alpha_reductase_inhibitor',
 '11-beta-hsd1_inhibitor',
 'acat_inhibitor',
 'acetylcholine_receptor_agonist',
 'acetylcholine_receptor_antagonist',
 'acetylcholinesterase_inhibitor',
 'adenosine_receptor_agonist',
 'adenosine_receptor_antagonist',
 'adenylyl_cyclase_activator',
 'adrenergic_receptor_agonist',
 'adrenergic_receptor_antagonist',
 'akt_inhibitor',
 'aldehyde_dehydrogenase_inhibitor',
 'alk_inhibitor',
 'ampk_activator',
 'analgesic',
 'androgen_receptor_agonist',
 'androgen_receptor_antagonist',
 'anesthetic_-_local',
 'angiogenesis_inhibitor',
 'angiotensin_receptor_antagonist',
 'anti-inflammatory',
 'antiarrhythmic',
 'antibiotic',
 'anticonvulsant',
 'antifungal',
 'antihistamine',
 'antimalarial',
 'antioxidant',
 'antiprotozoal',
 'antiviral',
 'apoptosis_stimulant',
 'aromatase_inhibitor',
 'atm_kinase_inhibitor',
 'atp-sensitive_potassium_channel_antagonist',
 'atp_synthase_inhibitor',
 'atpase_inhibitor',
 'atr_kinase_inhibitor',
 'aurora_kinase_inhibitor',
 '

In [14]:
def process_data(data):
    data = pd.get_dummies(data, columns=['cp_time','cp_dose'])
    return data

train_data = process_data(train_data)
test_data  = process_data(test_data)

feature_cols = [c for c in train_data.columns if c not in target_cols]
feature_cols = [c for c in feature_cols if c not in ['kfold','sig_id','cp_type']]

# feature_cols

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


In [15]:
train_losses = []
valid_losses = []
saved_model_paths = []

for seed in range(1, cfg.n_seeds+1):

    pl.seed_everything(seed)

    folds = train_data.copy()
    k_fold = MultilabelStratifiedKFold(n_splits=cfg.n_splits, shuffle=True, random_state=seed * 111)
    for n, (train_index, valid_index) in enumerate(k_fold.split(folds, folds[target_cols])):

        df_train = folds.iloc[train_index]
        df_valid = folds.iloc[valid_index]

        train_x = df_train[feature_cols].values.astype(np.float32)
        train_y = df_train[target_cols].values.astype(np.float32)
        train_tensor = torch.utils.data.TensorDataset(torch.tensor(train_x), torch.tensor(train_y)) 

        valid_x = df_valid[feature_cols].values.astype(np.float32)
        valid_y = df_valid[target_cols].values.astype(np.float32)
        valid_tensor = torch.utils.data.TensorDataset(torch.tensor(valid_x), torch.tensor(valid_y)) 

        train_dl = torch.utils.data.DataLoader(train_tensor, shuffle=True, batch_size=2 ** cfg.batch_size_exp)  
        valid_dl = torch.utils.data.DataLoader(valid_tensor, shuffle=False, batch_size=2 ** cfg.batch_size_exp)

        checkpoint_callback = pl.callbacks.ModelCheckpoint(monitor='val/loss', dirpath='./', filename=f's{seed}f{n}')
        callbacks = [
            checkpoint_callback,
            pl.callbacks.EarlyStopping(monitor=f'val/loss', patience=20)]

        trainer = pl.Trainer(gpus=1, max_epochs=100, callbacks=callbacks)

        lit_module = MoANeuralNetwork(train_x.shape[1], train_y.shape[1], cfg)
        trainer.fit(lit_module, train_dl, valid_dl)

        fold_train_loss = trainer.logged_metrics['train/loss']
        fold_valid_loss = trainer.logged_metrics['val/loss']
        train_losses.append(fold_train_loss)
        valid_losses.append(fold_valid_loss)
        print(f'Train: {fold_train_loss}, valid: {fold_valid_loss} for seed {seed}/{cfg.n_seeds}, fold {n+1}/{cfg.n_splits}')    

        saved_model_paths.append(checkpoint_callback.best_model_path)

https://ui.neptune.ai/mtszkw/kaggle-lish-moa/e/LISHMOA-1


NeptuneLogger will work in online mode
D:\conda\envs\lightning\lib\site-packages\sklearn\utils\validation.py:67: FutureWarning: Pass shuffle=True, random_state=7 as keyword args. From version 0.25 passing these as positional arguments will result in an error
  warnings.warn("Pass {} as keyword args. From version 0.25 "
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name | Type       | Params
------------------------------------
0 | net  | Sequential | 914 K 


Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 3c1019ae-c708-4a34-8b

Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 3c1019ae-c708-4a34-8b

Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 3c1019ae-c708-4a34-8b

...

Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 7c5f1253-ceb7-44d5-83

Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 7c5f1253-ceb7-44d5-83

D:\conda\envs\lightning\lib\site-packages\pytorch_lightning\utilities\distributed.py:45: UserWarning: Detected KeyboardInterrupt, attempting graceful shutdown...
  warnings.warn(*args, **kwargs)


Failed to send channel value.
Traceback (most recent call last):
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\channels\channels_values_sender.py", line 156, in _send_values
    self._experiment._send_channels_values(channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\experiments.py", line 1141, in _send_channels_values
    self._backend.send_channels_values(self, channels_with_values)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\utils.py", line 211, in wrapper
    return func(*args, **kwargs)
  File "D:\conda\envs\lightning\lib\site-packages\neptune\internal\backends\hosted_neptune_backend.py", line 573, in send_channels_values
    raise ChannelsValuesSendBatchError(experiment.id, batch_errors)
neptune.api_exceptions.ChannelsValuesSendBatchError: Received batch errors sending channels' values to experiment LISHMOA-1. Cause: Error(code=400, message='X-coordinates must be strictly increasing for channel: 7c5f1253-ceb7-44d5-83

KeyboardInterrupt: 

In [ ]:
print(f'Train loss: {np.mean(np.array(train_losses)):.5f} +- {np.std(np.array(train_losses)):.5f}')
print(f'Valid loss: {np.mean(np.array(valid_losses)):.5f} +- {np.std(np.array(valid_losses)):.5f}')

In [ ]:
saved_model_paths

## Submission

In [ ]:
test_tensor = torch.utils.data.TensorDataset(torch.tensor(test_data[feature_cols].values.astype(np.float32)))
test_dl     = torch.utils.data.DataLoader(test_tensor, shuffle=False, batch_size=1)


final_predictions = np.zeros((test_data.shape[0], len(target_cols)))

for model_path in saved_model_paths:
    saved_model = MoANeuralNetwork.load_from_checkpoint(
        model_path, input_size=len(feature_cols), output_size=len(target_cols), cfg=cfg)
    
    saved_model.eval()

    predictions = []
    for batch in test_dl:
        y_hat = saved_model(batch[0]).sigmoid().detach().squeeze().numpy()
        y_hat = np.clip(y_hat, 0.001, 0.999)
        predictions.append(y_hat)

    final_predictions += np.array(predictions)
    
final_predictions /= len(saved_model_paths)

print(final_predictions)
final_predictions.shape

In [ ]:
test_data

In [ ]:
df_submission = pd.read_csv(os.path.join(input_dir, 'sample_submission.csv'))
df_submission[target_cols] = final_predictions
df_submission.loc[test_data['cp_type']=='ctl_vehicle', target_cols] = 0.0

df_submission.to_csv('submission.csv', index=False)

df_submission

In [ ]:
kernel_stop = datetime.now()

print(kernel_stop - kernel_start)